# Profitable App Profiles for Google Play Markets

This project aims to perform a quick evaluation of what factors could affect the total number of installs for an app. Here we assume that the total number of installs can directly determain if one app is profitable since 1) if the app is not free, more download means higher profit and 2) even if the app is free more installs brings more user which mean any adds within the app have a higher exposure to the public and more people wolud subscribe to whatever services the app offers.

This project applies random forest regressor and tries to:

- Predict how many times an app is installed
- Observe what are the most important feature(s) affecting # installed



Besides, simple data exploration is performed for reference..

## Cleaning and Orgnizing the Data Set


In [1]:
from csv import reader
import pandas as pd
import numpy as np
### The Google Play data set ###
opened_file = open('googleplaystore.csv', encoding='utf8')
read_file = reader(opened_file)
android = list(read_file)
android_header = android[0]
android = android[1:]

In [2]:
# explore the list data easier
def explore_data(dataset: list, start: int, end: int, rows_and_columns=False):
    dataset_slice = dataset[start:end]    
    for row in dataset_slice:
        print(row)
        print('\n') 

    if rows_and_columns:
        print('Number of rows:', len(dataset))
        print('Number of columns:', len(dataset[0]))

In [3]:
# demostrate the function out put
print(android_header)
print('\n')
explore_data(android,0,3,True)

['App', 'Category', 'Rating', 'Reviews', 'Size', 'Installs', 'Type', 'Price', 'Content Rating', 'Genres', 'Last Updated', 'Current Ver', 'Android Ver']


['Photo Editor & Candy Camera & Grid & ScrapBook', 'ART_AND_DESIGN', '4.1', '159', '19M', '10,000+', 'Free', '0', 'Everyone', 'Art & Design', 'January 7, 2018', '1.0.0', '4.0.3 and up']


['Coloring book moana', 'ART_AND_DESIGN', '3.9', '967', '14M', '500,000+', 'Free', '0', 'Everyone', 'Art & Design;Pretend Play', 'January 15, 2018', '2.0.0', '4.0.3 and up']


['U Launcher Lite – FREE Live Cool Themes, Hide Apps', 'ART_AND_DESIGN', '4.7', '87510', '8.7M', '5,000,000+', 'Free', '0', 'Everyone', 'Art & Design', 'August 1, 2018', '1.2.4', '4.0.3 and up']


Number of rows: 10841
Number of columns: 13


In [4]:
#this data entry has incorrect formate according to disscussion section on Kaggle
del android[10472] # delete incorrect entry

### Data pre processing and Feature selection
Clean up the data and select apps that have an English name.
Create pandas DataFrame

1. Prepare feature, convert str to numerical data, and remove duplicate entries.

2. Make some catgorical data to one-hot formate

In [5]:
# Find if an app name is in English
def is_english(string):
    non_ascii = 0
    
    for character in string:
        if ord(character) > 127:
            non_ascii += 1
    
    if non_ascii > 3:
        return False
    else:
        return True
    
def creat_dataframe(data,data_header):
    #Create dataframe
    df_data = pd.DataFrame(data,columns=data_header)

    # Remove duplicate app entries
    df_data = df_data.loc[~df_data.index.duplicated(keep='first')]
    #Select English only Apps
    df_data[df_data['App'].apply(lambda x: is_english(x))]
    #df_data.set_index('App',inplace=True)
    return df_data

df_adroid = creat_dataframe(android,android_header)

#Convert str to numeric data
df_adroid['Rating'] = df_adroid['Rating'].str.findall(r'[0-9][.][0-9]')
df_adroid['Rating'] = [pd.to_numeric(x[0])  if len(x) >0 else None for x in df_adroid['Rating']]
#fill missing values use the average rating in each category
df_adroid['Rating'] = df_adroid.groupby('Category').transform(lambda x: x.fillna(x.mean()))
df_adroid['Rating'] = df_adroid['Rating'].apply(lambda x : float(x))

df_adroid['Reviews'] = pd.to_numeric(df_adroid['Reviews'])
df_adroid['Installs'] = pd.to_numeric(df_adroid['Installs'].apply(lambda x : x.split('+')[0].replace(",", "")))
df_adroid['Price'] = pd.to_numeric(df_adroid['Price'].apply(lambda x : x.split('$')[0].replace(",", "")))


# Correct the NaN value of this entry
df_adroid.loc[9148,'Type']='Free' 

#Make one hot variables
df_adroid = pd.concat([df_adroid,pd.get_dummies(df_adroid['Content Rating'])],axis = 1)
df_adroid = pd.concat([df_adroid,pd.get_dummies(df_adroid['Type'])],axis = 1)
df_adroid = pd.concat([df_adroid,pd.get_dummies(df_adroid['Category'])],axis = 1)

df_adroid.drop(columns=['Current Ver','Android Ver','Size','Genres','Last Updated','Content Rating','Price'],inplace=True)

In [6]:
df_adroid.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10840 entries, 0 to 10839
Data columns (total 47 columns):
App                    10840 non-null object
Category               10840 non-null object
Rating                 10840 non-null float64
Reviews                10840 non-null int64
Installs               10840 non-null int64
Type                   10840 non-null object
Adults only 18+        10840 non-null uint8
Everyone               10840 non-null uint8
Everyone 10+           10840 non-null uint8
Mature 17+             10840 non-null uint8
Teen                   10840 non-null uint8
Unrated                10840 non-null uint8
Free                   10840 non-null uint8
Paid                   10840 non-null uint8
ART_AND_DESIGN         10840 non-null uint8
AUTO_AND_VEHICLES      10840 non-null uint8
BEAUTY                 10840 non-null uint8
BOOKS_AND_REFERENCE    10840 non-null uint8
BUSINESS               10840 non-null uint8
COMICS                 10840 non-null uint8
COMMUN

## Data exploration

Group the data via their category and compute:
1. average rating
2. total number of apps in one category
3. average review
4. average total insalls

In [7]:
Catgorical = df_adroid.groupby('Category').mean()[['Rating','Reviews','Installs',]]
Catgorical['Count# of App'] = df_adroid.groupby('Category').apply(lambda x: len(x))
Catgorical.reset_index(inplace = True)
#sort according to average installs
Catgorical.sort_values(by='Installs',
                       ascending=False,
                       axis=0).head(20)

Category    Rating       Reviews      Installs  Count# of App
6         COMMUNICATION  4.158537  2.107138e+06  8.435989e+07            387
27               SOCIAL  4.255598  2.105903e+06  4.769447e+07            295
31        VIDEO_PLAYERS  4.063750  6.307439e+05  3.555430e+07            175
25         PRODUCTIVITY  4.211396  2.691438e+05  3.343418e+07            424
14                 GAME  4.286326  1.385859e+06  3.066960e+07           1144
24          PHOTOGRAPHY  4.192114  6.373631e+05  3.011417e+07            335
30     TRAVEL_AND_LOCAL  4.109292  2.427051e+05  2.662359e+07            258
21   NEWS_AND_MAGAZINES  4.132189  1.922292e+05  2.648876e+07            283
9         ENTERTAINMENT  4.126174  3.971688e+05  1.925611e+07            149
29                TOOLS  4.047411  3.240629e+05  1.358573e+07            843
26             SHOPPING  4.259664  4.424662e+05  1.249173e+07            260
3   BOOKS_AND_REFERENCE  4.346067  9.506090e+04  8.318050e+06            231
23      PERSONALIZATION  4.335987  2.279238e+05  5.932385e+06            392
8             EDUCATION  4.389032  2.538191e+05  5.586231e+06            156
19  MAPS_AND_NAVIGATION  4.051613  2.237902e+05  5.286729e+06            137
11               FAMILY  4.192272  2.080255e+05  5.201959e+06           1972
32              WEATHER  4.244000  1.781065e+05  5.196348e+06             82
15   HEALTH_AND_FITNESS  4.277104  1.111253e+05  4.642441e+06            341
28               SPORTS  4.223511  1.844536e+05  4.560350e+06            384
12              FINANCE  4.131889  4.795281e+04  2.395215e+06            366

Looking at the table above, we can see that communication has the highest average install and family has the most number of apps. This information can give some idea of which category are popular and/or more competitor. However, it doesn't say which factor affect the number of actual downloads.   

In [8]:
#Apps distribution amoung categories
import matplotlib.pyplot as plt
fig, axs = plt.subplots(figsize = [12,10])
group_dist = df_adroid.groupby('Category').size()
group_names = group_dist.index.values
axs.bar(group_names,group_dist)
plt.xticks(rotation=90)
plt.show()

<Figure size 1200x1000 with 1 Axes>

## Training Data with Random Forest Regression

- The madel is train using random forest regression.
- The data is normalized between 0 and 1.
- 1/3 of the data are selected as test set.
- Grid search for finding the hyper patameters that perform better.
- Evaluate the performance wiht R2 score

In [9]:
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.ensemble import RandomForestRegressor
from sklearn.preprocessing import normalize
from sklearn.metrics import r2_score

In [10]:
# Prep input data
X = df_adroid.drop(['App','Installs','Type','Category'],axis = 1)
y = df_adroid['Installs']

In [11]:
#normalizing features
X = pd.DataFrame(normalize(X,norm='max',axis=0),columns=X.columns)

In [12]:
# Split data to train and test sets with random selection
X_train, X_test, y_train, y_test = train_test_split(X, y, 
                                                    test_size=0.33, 
                                                    random_state=42)

In [13]:
#Grid search for max depth and # of estimators
parameters = {'max_depth':[2, 5, 10, 15, 20, 25, 30],
              'n_estimators':[100, 120, 150, 200]}
Rf = RandomForestRegressor(random_state=0)
grid_search = GridSearchCV(Rf,param_grid=parameters,
                           scoring='r2',cv=10)
grid_search.fit(X_train, y_train)

GridSearchCV(cv=10, error_score='raise-deprecating',
       estimator=RandomForestRegressor(bootstrap=True, criterion='mse', max_depth=None,
           max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators='warn', n_jobs=None,
           oob_score=False, random_state=0, verbose=0, warm_start=False),
       fit_params=None, iid='warn', n_jobs=None,
       param_grid={'max_depth': [2, 5, 10, 15, 20, 25, 30], 'n_estimators': [100, 120, 150, 200]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='r2', verbose=0)

In [14]:
print("parameters:")
print(parameters)
print("Best score: %0.3f" % grid_search.best_score_)
print("Best parameters set:")
best_parameters=grid_search.best_estimator_.get_params()
for param_name in sorted(parameters.keys()):
    print("\t%s: %r" % (param_name, best_parameters[param_name]))

print('--------------------------------------------')    
print(grid_search.best_estimator_.get_params())

parameters:
{'max_depth': [2, 5, 10, 15, 20, 25, 30], 'n_estimators': [100, 120, 150, 200]}
Best score: 0.838
Best parameters set:
	max_depth: 30
	n_estimators: 200
--------------------------------------------
{'bootstrap': True, 'criterion': 'mse', 'max_depth': 30, 'max_features': 'auto', 'max_leaf_nodes': None, 'min_impurity_decrease': 0.0, 'min_impurity_split': None, 'min_samples_leaf': 1, 'min_samples_split': 2, 'min_weight_fraction_leaf': 0.0, 'n_estimators': 200, 'n_jobs': None, 'oob_score': False, 'random_state': 0, 'verbose': 0, 'warm_start': False}


In [15]:
#Evaluate model performance with test set
best_model = grid_search.best_estimator_
prediction = best_model.predict(X_test)
print("R2 Score: %0.3f" % (r2_score(y_test,prediction)))

R2 Score: 0.884


In [16]:
# Feature importance 
pd.Series(best_model.feature_importances_,
          index = X_train.columns).sort_values(ascending=False).head(20)

Reviews                0.674185
Rating                 0.175100
PHOTOGRAPHY            0.023318
PRODUCTIVITY           0.018285
GAME                   0.017532
COMMUNICATION          0.016685
Teen                   0.015966
NEWS_AND_MAGAZINES     0.010495
TRAVEL_AND_LOCAL       0.009982
TOOLS                  0.008067
Everyone               0.005694
FAMILY                 0.004782
Everyone 10+           0.003703
ENTERTAINMENT          0.003518
SOCIAL                 0.002813
VIDEO_PLAYERS          0.002659
BUSINESS               0.002092
Mature 17+             0.001720
HEALTH_AND_FITNESS     0.001407
BOOKS_AND_REFERENCE    0.000622
dtype: float64

## Conclusion

The R2 score is not yet optimal in this project. It can be improved by more feature extraction, tuning hyper-parameters of the model, training using other regression models...etc. One reason is that the total installs of this data set are in open-ended formate like 1,000+, 50,000+, and 1000,000+. The data may be not perfectly precise. However, this project demonstrates a preliminary investigation to the data set and has a quick insight into what is going on with it. This provides the basic idea of the data set and further complex models can be built based on it.

The importance of feature is sorted as shown above. The most important feature, reviews, can be referred to as the hotness of an app regardless of good reviews or bad ones. Similarly, the rating of an app could be a direct factor from users. Therefore, It is no surprise that review and rating play a big part that decides the total download of an app. The interesting part is the rest feature that is one-hot encoding for each category. Rather just looking at the average total installs of each category, This could be an indication of which type of app ones can consider developing since the total # of installs is relative which category an app belongs to. As a result, one can use the result to have a quick idea if an app will be more likely profitable.


## Visualze the trees 

In [17]:
from sklearn.tree import export_graphviz
# Export as dot file
export_graphviz(best_model.estimators_[0], out_file='tree.png', 
                feature_names = X_train.columns,
                rounded = True, proportion = False, 
                precision = 2, filled = True)

In [18]:
import pydot
(graph,) = pydot.graph_from_dot_file('tree.dot')
graph.write_png('tree.png')

In [19]:
# Display in jupyter notebook
from IPython.display import Image
Image(filename = 'tree.png')